In [2]:
import folium

In [3]:
#from pyproj import CRS
import fiona.crs
import geopandas as gpd
import matplotlib.pyplot as plt
import numpy as np
import requests
import geojson
import urllib.request as request

In [4]:
def get_census_bounds():
    url = 'https://opendata.arcgis.com/datasets/de58dc3e1efc49b782ab357e044ea20c_9.geojson'
    census_bounds = gpd.read_file(url)
    census_columns = ['NAME10', 'SHAPE_Area', 'geometry']
    census_bounds_cleaned = census_bounds.loc[:,census_columns]
    census_bounds_cleaned['NAME10'] = census_bounds_cleaned['NAME10'].astype(float)
    return census_bounds_cleaned

In [5]:
census_bounds = get_census_bounds()

In [6]:
census_bounds.head()

NAME10    SHAPE_Area                                           geometry
0    25.0  1.059462e+07  POLYGON ((-122.29602 47.69023, -122.29608 47.6...
1    26.0  1.339838e+07  POLYGON ((-122.30817 47.69031, -122.30947 47.6...
2    56.0  3.212601e+07  POLYGON ((-122.39300 47.63956, -122.39421 47.6...
3    68.0  7.729233e+06  POLYGON ((-122.35070 47.63994, -122.35130 47.6...
4    60.0  1.413816e+07  POLYGON ((-122.34279 47.64320, -122.34280 47.6...

In [7]:
def get_zipcode_bounds():
        zipcodes_url = 'https://opendata.arcgis.com/datasets/83fc2e72903343aabff6de8cb445b81c_2.geojson'
        zipcodes = gpd.read_file(zipcodes_url)

        zipcodes_columns = ['ZIPCODE', 'SHAPE_Area', 'geometry']
        zipcodes_cleaned = zipcodes.loc[:,zipcodes_columns]
        zipcodes_cleaned['ZIPCODE'] = zipcodes_cleaned['ZIPCODE'].astype(int)
        zipcodes_cleaned.head()

        census_bounds_cleaned = get_census_bounds()
        zips = gpd.sjoin(zipcodes_cleaned, census_bounds_cleaned, op='intersects')
        zips_columns = ['ZIPCODE', 'NAME10', 'SHAPE_Area_left', 'geometry']
        zips = zips[zips_columns]

        zips = zips.dissolve(by='ZIPCODE')
        return zips

In [8]:
zip_bounds = get_zipcode_bounds()

In [9]:
zip_bounds.head()

geometry  NAME10  \
ZIPCODE                                                              
98101    POLYGON ((-122.34598 47.60892, -122.34490 47.6...   74.02   
98102    POLYGON ((-122.33574 47.64203, -122.33108 47.6...   74.02   
98103    POLYGON ((-122.35808 47.69966, -122.35741 47.6...   45.00   
98104    POLYGON ((-122.34105 47.59627, -122.34031 47.5...   84.00   
98105    MULTIPOLYGON (((-122.32859 47.66646, -122.3285...   41.00   

         SHAPE_Area_left  
ZIPCODE                   
98101       1.470012e+07  
98102       4.322189e+07  
98103       1.440083e+08  
98104       2.108730e+07  
98105       9.703543e+07

In [10]:
url_list = ['https://opendata.arcgis.com/datasets/7015d5d46a284f94ac05c2ea4358bcd7_0.geojson',
            'https://opendata.arcgis.com/datasets/5fc63b2a48474100b560a7d98b5097d7_1.geojson',
            'https://opendata.arcgis.com/datasets/27af9a2485c5442bb061fa7e881d7022_2.geojson',
            'https://opendata.arcgis.com/datasets/4f62515558174f53979b3be0335004d3_3.geojson',
            'https://opendata.arcgis.com/datasets/29f801d03c9b4b608bca6a8e497278c3_4.geojson',
            'https://opendata.arcgis.com/datasets/a0019dd0d6464747a88921f5e103d509_5.geojson',
            'https://opendata.arcgis.com/datasets/40bcfbc4054549ebba8b5777bbdd40ff_6.geojson',
            'https://opendata.arcgis.com/datasets/16cedd233d914118a275c6510115d466_7.geojson',
            'https://opendata.arcgis.com/datasets/902fd604ecf54adf8579894508cacc68_8.geojson',
            'https://opendata.arcgis.com/datasets/170b764c52f34c9497720c0463f3b58b_9.geojson',
            'https://opendata.arcgis.com/datasets/2c37babc94d64bbb938a9b520bc5538c_10.geojson',
            'https://opendata.arcgis.com/datasets/a35aa9249110472ba2c69cc574eff984_11.geojson']

In [11]:
def get_gdf(year):
    '''Enter the desired year to download the traffic flow count
    data for that year. Example: enter '7' for the year 2007.
    '''
    num = year-7
    gdf_year = gpd.read_file(url_list[num])
    if year == 11:
        gdf_year = gdf_year.rename(columns={"YEAR_" : 'YEAR'})
    if year == 12:
        gdf_year = gdf_year.rename(columns={'STDY_YEAR' : 'YEAR'})
    if year == 15 or year == 16:
        gdf_year = gdf_year.rename(columns={"COUNTAAWDT" : 'AAWDT', "FLOWSEGID" : "GEOBASID", 'FIRST_STNAME_ORD' : 'STNAME'})
        gdf_year = gdf_year[['AAWDT', 'GEOBASID', 'STNAME', 'SHAPE_Length', 'geometry']]
        if year == 15:
            year_list = ['2015']*len(gdf_year)
            gdf_year['YEAR'] = year_list
        elif year == 16:
            year_list = ['2016']*len(gdf_year)
            gdf_year['YEAR'] = year_list
    elif year == 17 or year == 18:
        gdf_year = gdf_year.rename(columns={"AWDT" : 'AAWDT', "FLOWSEGID" : "GEOBASID", 'STNAME_ORD' : 'STNAME'})
        gdf_year = gdf_year[['AAWDT', 'GEOBASID', 'STNAME', 'SHAPE_Length', 'geometry']]
        if year == 17:
            year_list = ['2017']*len(gdf_year)
            gdf_year['YEAR'] = year_list
        elif year == 18:
            year_list = ['2018']*len(gdf_year)
            gdf_year['YEAR'] = year_list
    #df_year_AAWDT = df_year['AAWDT'].values
    #df_year_geobase = df_year['GEOBASID'].values
    #df_year_dist = df_year['SHAPE_Length'].values
    gdf_year = gdf_year[[ 'YEAR', 'AAWDT', 'GEOBASID', 'STNAME', 'SHAPE_Length', 'geometry']]
    return gdf_year #, df_year_AAWDT, df_year_geobase, df_year_dist

In [12]:
gdf_15 = get_gdf(15)

In [21]:
test = gdf_15['YEAR'].unique().astype(int)[0]

In [22]:
inputs = list(range(7,19))
years = list(range(2007,2019))
year_dict = dict(zip(inputs,years))

In [24]:
assert year_dict.get(15) == test, 'oops'

In [17]:
city_by_zip = gpd.sjoin(zip_bounds, gdf_15, op='intersects')

In [18]:
traffic_zones = city_by_zip.dissolve(by='ZIPCODE', aggfunc = sum)
traffic_zones.reset_index(inplace = True)
traffic_zones.head()

ZIPCODE                                           geometry    NAME10  \
0    98101  POLYGON ((-122.34598 47.60892, -122.34490 47.6...  13323.60   
1    98102  POLYGON ((-122.33574 47.64203, -122.33108 47.6...   2738.74   
2    98103  POLYGON ((-122.35808 47.69966, -122.35741 47.6...   5670.00   
3    98104  POLYGON ((-122.34105 47.59627, -122.34031 47.5...  13944.00   
4    98105  MULTIPOLYGON (((-122.32859 47.66646, -122.3285...   6560.00   

   SHAPE_Area_left  index_right         AAWDT  GEOBASID   SHAPE_Length  
0     2.646022e+09       196214  1.877668e+06  155333.0   74844.695909  
1     1.599210e+09        25633  4.782904e+05   47234.0   65590.492939  
2     1.814505e+10        51768  1.880369e+06  200939.0  179316.992061  
3     3.500492e+09       211992  1.847450e+06  109732.0   82763.478579  
4     1.552567e+10        81293  1.762661e+06  239536.0  165116.392503

In [19]:
#traffic_zones.crs = fiona.crs.from_epsg(4326)
traffic_zones.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [26]:
traffic_zones = traffic_zones[['GEOBASID', 'AAWDT', 'ZIPCODE', 'geometry']]
traffic_zones_json = traffic_zones.to_json()
traffic_zones_json

'{"type": "FeatureCollection", "features": [{"id": "0", "type": "Feature", "properties": {"AAWDT": 1877668.021429, "GEOBASID": 155333.0, "ZIPCODE": 98101}, "geometry": {"type": "Polygon", "coordinates": [[[-122.34597868938772, 47.608920239303366], [-122.3448958059157, 47.60892029324418], [-122.34475509741763, 47.60892272115523], [-122.34443556740094, 47.6091306982063], [-122.3445389702794, 47.60919189173416], [-122.34482280946305, 47.60935985394823], [-122.34490177672335, 47.60940655765578], [-122.34531813146658, 47.60965279812794], [-122.34547284853689, 47.609744296143504], [-122.34566322725934, 47.609856889713875], [-122.34527003971598, 47.61017401676882], [-122.34526987075856, 47.61017391793202], [-122.34500452523183, 47.610397200785506], [-122.34500194552935, 47.61039558686249], [-122.34452068472727, 47.610094031016274], [-122.34372860355336, 47.6095959578167], [-122.34372460679307, 47.60959344170888], [-122.34354149155025, 47.60971262164593], [-122.34354117497966, 47.6097128729362

In [23]:
type(traffic_zones['AAWDT'][0])

numpy.float64

In [47]:
variable = 'AAWDT'
traffic_zones=traffic_zones.sort_values(by=variable, ascending=True)
colormap = folium.LinearColormap(colors=['green','yellow','red'], vmin=traffic_zones[variable].min(),
                                 vmax=traffic_zones[variable].max()).to_step(n=10)
colormap.caption = "2015 Seattle Traffic Flow Counts"

In [19]:
centroid=traffic_zones.geometry.centroid

<ipython-input-19-987927e6528d>:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid=traffic_zones.geometry.centroid


In [48]:
centroid=traffic_zones.geometry.centroid

m=folium.Map(location=[centroid.y.mean(), centroid.x.mean()], zoom_start=10, tiles='cartodbpositron')

folium.GeoJson(traffic_zones[['geometry','NAME10',variable]],
               name='Average Annual Weekly Daily Traffic Flow 2015',
               style_function=lambda x: {"weight":0.5, 'color':'white','fillColor':colormap(x['properties'][variable]), 'fillOpacity':0.4},
              highlight_function=lambda x: {'weight':3, 'color':'black'},
               smooth_factor=2.0,
              tooltip=folium.features.GeoJsonTooltip(fields=['NAME10',variable],
                                              aliases=['Census Tract','2015 Aggregate Traffic Flow'], 
                                              labels=True, 
                                              sticky=True,
                                              toLocaleString=True
                                             )
              ).add_to(m)


colormap.add_to(m)

folium.LayerControl(autoZIndex=True, collapsed=True).add_to(m)

m

<ipython-input-48-e52a45f4513c>:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid=traffic_zones.geometry.centroid


In [49]:
outfp = "choropleth_map_v2.html"
m.save(outfp)

In [27]:
# Create a Map instance
m = folium.Map(location=[47.65, -122.3], tiles = 'cartodbpositron', zoom_start=10, control_scale=True)

# Plot a choropleth map
# Notice: 'geoid' column that we created earlier needs to be assigned always as the first column
folium.Choropleth(
    geo_data=traffic_zones_json,
    name='Average Annual Weekly Daily Traffic Flow 2015',
    data=traffic_zones,
    columns=['GEOBASID', 'AAWDT'],
    key_on='feature.properties.GEOBASID',
    fill_color='RdYlBu_r',
    fill_opacity=0.7,
    line_opacity=0.2,
    line_color='white', 
    line_weight=2,
    highlight=False, 
    smooth_factor=1.0,
    #threshold_scale=[100, 250, 500, 1000, 2000],
    legend_name= 'Traffic Counts').add_to(m)

# Convert points to GeoJson
folium.features.GeoJson(traffic_zones,  
                        name='Labels',
                        style_function=lambda x: {'color':'transparent','fillColor':'transparent','weight':0},
                        tooltip=folium.features.GeoJsonTooltip(fields=['ZIPCODE','AAWDT'],
                                                                aliases = ['Zipcode','Traffic Count'],
                                                                labels=True,
                                                                sticky=False
                                                                            )
                       ).add_to(m)

#Show map
m

In [73]:
outfp = "choropleth_map.html"
m.save(outfp)

In [32]:
import altair as alt
import json

alt.themes.enable('opaque')




ThemeRegistry.enable('opaque')

In [43]:
traffic_zones['centroid_lon'] = traffic_zones['geometry'].centroid.x
traffic_zones['centroid_lat'] = traffic_zones['geometry'].centroid.y
traffic_zones.head()

<ipython-input-43-36737b98dbea>:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  traffic_zones['centroid_lon'] = traffic_zones['geometry'].centroid.x
<ipython-input-43-36737b98dbea>:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  traffic_zones['centroid_lat'] = traffic_zones['geometry'].centroid.y


GEOBASID          AAWDT  NAME10  \
0  17120.0  200687.184322       1   
1  22138.0  190009.612137      10   
2   9273.0  356718.912824  100.01   
3   9538.0  262826.787822  100.02   
4   4158.0  176011.905119     101   

                                            geometry  centroid_lon  \
0  POLYGON ((-122.29654 47.73198, -122.29653 47.7...   -122.288742   
1  POLYGON ((-122.30218 47.70163, -122.30191 47.7...   -122.296063   
2  POLYGON ((-122.31733 47.56350, -122.31728 47.5...   -122.305026   
3  POLYGON ((-122.31607 47.58094, -122.31606 47.5...   -122.309571   
4  POLYGON ((-122.29690 47.56783, -122.29690 47.5...   -122.283006   

   centroid_lat  
0     47.726278  
1     47.706409  
2     47.567995  
3     47.576581  
4     47.566149

In [49]:
choro_json = json.loads(traffic_zones.to_json())
choro_data = alt.Data(values=choro_json['features'])